# sam3d-obj notebook

This notebook is prepared for SAM 3D Objects experiments.


In [4]:
import time
import subprocess
import psutil
from IPython.display import clear_output

try:
    import torch
except Exception:
    torch = None

def show_status():
    try:
        gpu = subprocess.check_output([
            'nvidia-smi',
            '--query-gpu=timestamp,name,memory.used,memory.total,utilization.gpu',
            '--format=csv,noheader,nounits',
        ]).decode().strip()
        print('GPU:', gpu)
    except Exception as exc:
        print('GPU: nvidia-smi unavailable:', exc)

    vm = psutil.virtual_memory()
    print(f'RAM: {vm.used/1e9:.2f} / {vm.total/1e9:.2f} GB ({vm.percent}%)')

    if torch is not None and torch.cuda.is_available():
        alloc = torch.cuda.memory_allocated() / 1e9
        peak = torch.cuda.max_memory_allocated() / 1e9
        print(f'Torch GPU mem: {alloc:.2f} GB (peak {peak:.2f} GB)')

show_status()

# Live refresh (stop with Interrupt):
# while True:
#     clear_output(wait=True)
#     show_status()
#     time.sleep(1)


GPU: 2026/01/12 20:38:41.631, NVIDIA L4, 259, 23034, 0
RAM: 8.01 / 56.86 GB (14.1%)
Torch GPU mem: 0.00 GB (peak 0.00 GB)


In [5]:
import torch
print(torch.cuda.memory_allocated()/1e9, "GB")
print(torch.cuda.max_memory_allocated()/1e9, "GB")


0.0 GB
0.0 GB


In [4]:
%pip install -U --force-reinstall "huggingface_hub>=0.19.3,<1.0"


  Using cached huggingface_hub-0.36.0-py3-none-any.whl.metadata (14 kB)
  Using cached packaging-25.0-py3-none-any.whl.metadata (3.3 kB)
  Using cached pyyaml-6.0.3-cp311-cp311-manylinux2014_x86_64.manylinux_2_17_x86_64.manylinux_2_28_x86_64.whl.metadata (2.4 kB)
  Using cached requests-2.32.5-py3-none-any.whl.metadata (4.9 kB)
  Using cached tqdm-4.67.1-py3-none-any.whl.metadata (57 kB)
  Using cached hf_xet-1.2.0-cp37-abi3-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (4.9 kB)
  Using cached charset_normalizer-3.4.4-cp311-cp311-manylinux2014_x86_64.manylinux_2_17_x86_64.manylinux_2_28_x86_64.whl.metadata (37 kB)
  Using cached idna-3.11-py3-none-any.whl.metadata (8.4 kB)
  Using cached urllib3-2.6.3-py3-none-any.whl.metadata (6.9 kB)
  Using cached certifi-2026.1.4-py3-none-any.whl.metadata (2.5 kB)
Using cached huggingface_hub-0.36.0-py3-none-any.whl (566 kB)
Using cached hf_xet-1.2.0-cp37-abi3-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (3.3 MB)
Using cached packaging-

In [2]:
import os, sys
from pathlib import Path

# Jupyter kernel 里没有 CONDA_PREFIX，手动补
os.environ.setdefault("CONDA_PREFIX", sys.prefix)

# CUDA_HOME 优先用系统 CUDA，不存在再用 CONDA_PREFIX
if "CUDA_HOME" not in os.environ:
    os.environ["CUDA_HOME"] = "/usr/local/cuda" if Path("/usr/local/cuda").exists() else os.environ["CONDA_PREFIX"]


In [5]:
import sys

sys.path.append("/content/sources/sam-3d-objects/notebook")
from inference import Inference, load_image, load_mask

image_path = "/content/sam3d-ready/notebook/example/kids-room/image.jpg"
mask_path = "/content/sam3d-ready/notebook/example/kids-room/0.png"

config_path = "/content/sources/sam-3d-objects/checkpoints/hf/pipeline.yaml"
inference = Inference(config_path, compile=False)

image = load_image(image_path)
mask = load_mask(mask_path)


2026-01-12 20:49:17.043 | INFO     | sam3d_objects.pipeline.inference_pipeline:set_attention_backend:17 - GPU name is NVIDIA L4
2026-01-12 20:49:18.075 | WARNING  | sam3d_objects.data.dataset.tdfy.preprocessor:__post_init__:51 - No rgb pointmap normalizer provided, using scale + shift 
2026-01-12 20:49:18.076 | WARNING  | sam3d_objects.data.dataset.tdfy.preprocessor:__post_init__:51 - No rgb pointmap normalizer provided, using scale + shift 
2026-01-12 20:49:18.124 | WARNING  | sam3d_objects.data.dataset.tdfy.preprocessor:__post_init__:51 - No rgb pointmap normalizer provided, using scale + shift 
/content/sam3d-ready/micromamba/envs/sam3d-unified/lib/python3.11/site-packages/moge/model/v1.py:171: UserWarning: The following deprecated/invalid arguments are ignored: {'output_mask': True, 'split_head': True}
  warnings.warn(f"The following deprecated/invalid arguments are ignored: {deprecated_kwargs}")
2026-01-12 20:49:48.026 | WARNING  | sam3d_objects.data.dataset.tdfy.preprocessor:__po

In [6]:
output = inference(image, mask, seed=42)

out_ply = "/content/sam3d-ready/notebook/example/kids-room/splat.ply"
output["gs"].save_ply(out_ply)
print("saved:", out_ply)


2026-01-12 20:50:46.494 | INFO     | sam3d_objects.pipeline.inference_pipeline:sample_sparse_structure:664 - Sampling sparse structure: inference_steps=25, strength=7, interval=[0, 500], rescale_t=3, cfg_strength_pm=0.0
2026-01-12 20:50:46.495 | INFO     | sam3d_objects.pipeline.inference_pipeline:get_condition_input:633 - Running condition embedder ...
2026-01-12 20:50:46.708 | INFO     | sam3d_objects.pipeline.inference_pipeline:get_condition_input:637 - Condition embedder finishes!
2026-01-12 20:50:58.250 | INFO     | sam3d_objects.pipeline.inference_pipeline:sample_sparse_structure:714 - Downsampled coords from 12695 to 9849
2026-01-12 20:50:58.278 | INFO     | sam3d_objects.pipeline.inference_pipeline_pointmap:run:437 - Rescaling scale by 1 after downsampling
2026-01-12 20:50:58.279 | INFO     | sam3d_objects.pipeline.inference_pipeline:sample_slat:744 - Sampling sparse latent: inference_steps=25, strength=1, interval=[0, 500], rescale_t=1
2026-01-12 20:50:58.280 | INFO     | sam3

saved: /content/sam3d-ready/notebook/example/kids-room/splat.ply


In [9]:
# 3DGS PLY preview with Plotly (auto-install plyfile if missing)
import numpy as np
import plotly.graph_objects as go
import plotly.io as pio

pio.renderers.default = "notebook_connected"

# Auto-install plyfile only if missing
try:
    import plyfile  # noqa: F401
except Exception:
    import sys, subprocess
    subprocess.check_call([sys.executable, "-m", "pip", "install", "plyfile"])
    import plyfile  # noqa: F401

from plyfile import PlyData

ply_path = "/content/sam3d-ready/notebook/example/kids-room/splat.ply"

ply = PlyData.read(ply_path)
v = ply["vertex"].data
pts = np.stack([v["x"], v["y"], v["z"]], axis=1)

names = v.dtype.names or ()
rgb = None
if {"red", "green", "blue"}.issubset(names):
    rgb = np.stack([v["red"], v["green"], v["blue"]], axis=1).astype(np.float32)
    if rgb.max() > 1.0:
        rgb /= 255.0
elif {"f_dc_0", "f_dc_1", "f_dc_2"}.issubset(names):
    f_dc = np.stack([v["f_dc_0"], v["f_dc_1"], v["f_dc_2"]], axis=1).astype(np.float32)
    C0 = 0.28209479177387814  # SH DC coefficient
    rgb = np.clip(f_dc * C0 + 0.5, 0.0, 1.0)

# Sample for responsiveness
max_points = 200_000
if len(pts) > max_points:
    idx = np.random.choice(len(pts), max_points, replace=False)
    pts = pts[idx]
    if rgb is not None:
        rgb = rgb[idx]

if rgb is None:
    colors = "rgb(80, 120, 200)"
else:
    colors = [f"rgb({int(r*255)},{int(g*255)},{int(b*255)})" for r, g, b in rgb]

fig = go.Figure(data=[go.Scatter3d(
    x=pts[:, 0], y=pts[:, 1], z=pts[:, 2],
    mode="markers", marker=dict(size=1, color=colors)
)])
fig.update_layout(scene_aspectmode="data")
fig.show(config={"scrollZoom": True})
